In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:98% !important; }</style>"))
display(HTML("<style>.output_result { max-width:98% !important; }</style>"))


# Code

## Imports

In [2]:
import pandas as pd
import numpy as np
import datetime
from collections import Counter
from tqdm.notebook import tqdm
import nltk
from nltk.corpus import stopwords
from nltk.util import ngrams, bigrams, trigrams
import statistics as stat
import seaborn as sns
import re
from nltk.stem.wordnet import WordNetLemmatizer
import plotly.colors as colors
import dataframe_image as dfi

# Set default color palette
colors_plotly_default = colors.qualitative.Plotly

main_path_mac = '/Users/philippmetzger/Documents/GitHub/battery_patents/'
main_path_ssd = '/Volumes/Samsung Portable SSD T3 Media/'

import sys
packages_path = main_path_mac+'/07 Packages'
sys.path.append(packages_path)

from helpers import (current_time_string,
                              image_saver,
                              country_labels_dict,
                              ctry_code_name_dict,
                              message,
                              numbers_dict)


## Read the whole dataset and reduce it to what we are interested in

In [3]:
# Read the whole dataset
dataset_name = 'data_batteries_2022-01-12_2001_ipf_only_classes_query_and_technologies_tagged'

path = main_path_ssd+'Dataset saves/04 From 15 Nov 2021 (release of 2021 Autumn edition)/01 Preprocessed/03 ipf only, classes query and technologies tagged/'+dataset_name+'.csv'

print('Loading data from:')
print(path)

data = pd.read_csv(path, delimiter = ";", low_memory = False, na_values=['', ' ', '  '], keep_default_na = False)

print('Number of rows:', len(data))

print('Distinct values in column "granted":', pd.unique(data['granted']))

# Reduce it to what we are interested in
a = (data['non_active_parts_electrodes_secondary_cells'] == 1)
b = (data['charging'] == 1)
c = (data['is_Redox flow'] == 1)
d = (data['is_Nickel–hydrogen'] == 1)

data_reduced = data[a | b | c | d].copy()
del data
data = data_reduced


Loading data from:
/Volumes/Samsung Portable SSD T3 Media/Dataset saves/04 From 15 Nov 2021 (release of 2021 Autumn edition)/01 Preprocessed/03 ipf only, classes query and technologies tagged/data_batteries_2022-01-12_2001_ipf_only_classes_query_and_technologies_tagged.csv
Number of rows: 2238481
Distinct values in column "granted": ['N' 'Y']


## Sort it by ['dobdb_family_id', 'earliest_publn_date']

In [4]:
data = data.sort_values(by = ['docdb_family_id', 'earliest_publn_date'])


## Reduce to years we are interested in

In [5]:
print(set(data['earliest_publn_year_this_family_id']))


{1999, 2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019}


In [6]:
data_reduced = data[data['earliest_publn_year_this_family_id'] >= 2000].copy()
del data
data = data_reduced


In [7]:
print(set(data['earliest_publn_year_this_family_id']))


{2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019}


In [8]:
only_granted = False


## In appln_abstract and appln_title: Replace NaNs with '  '

In [9]:
data['appln_abstract'].fillna('  ', inplace=True)
data['appln_title'].fillna('  ', inplace=True)


## Just a comment

I got confused because "alkaline" comes up in the terms with decreasing frequency.

Probably because there are also Secondary Alkaline Batteries.

https://www.sciencedirect.com/topics/materials-science/secondary-alkaline-battery
(2009):

"In the future, secondary alkaline batteries will come under increasing competitive pressure from lithium-ion 
systems in an expanding number of applications."


## Infer our time frame from data

In [10]:
year_begin = min(data['earliest_publn_year_this_family_id'])
year_end = max(data['earliest_publn_year_this_family_id'])

years = list(range(year_begin, year_end + 1))
print(years)


[2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019]


## Of every family, keep only the last english, non-nan title and abstract

In [11]:
family_ids = pd.unique(data['docdb_family_id'])

# Create two dictionaries containing an empty set for each year
titles_dict = {}
abstracts_dict = {} 
for year in years:
    
    titles_dict[year] = set()
    abstracts_dict[year] = set()
    
for family_id in tqdm(family_ids):
    
    data_this_family_id = data[data['docdb_family_id']==family_id]
    
    earliest_publn_year_this_family_id = list(set(data_this_family_id['earliest_publn_year_this_family_id']))[0]
    
    
    # Get titles
    
    titles_this_family_id = list(pd.unique(data_this_family_id[
        data_this_family_id['appln_title_lg']=='en'
    ]['appln_title']))
    try:
        titles_this_family_id.remove('  ')
    except:
        pass
    
    try:
        last_title_this_family_id = titles_this_family_id[-1]
    except:
        pass
    
    titles_dict[earliest_publn_year_this_family_id].add(last_title_this_family_id)
    
    
    # Get abstracts
    
    abstracts_this_family_id = list(pd.unique(data_this_family_id[
        data_this_family_id['appln_abstract_lg']=='en'
    ]['appln_abstract']))
    try:
        abstracts_this_family_id.remove('  ')
    except:
        pass
    
    try:
        last_abstract_this_family_id = abstracts_this_family_id[-1]
    except:
        pass
    
    abstracts_dict[earliest_publn_year_this_family_id].add(last_abstract_this_family_id)
    

  0%|          | 0/92700 [00:00<?, ?it/s]

## Get titles and abstracts counts for each year

In [12]:
# Old version (before I implemented to use only the most recent titles / abstracts):

if False:
    
    titles_counts = []
    abstracts_counts = []

    for year in tqdm(years):

        # Get unique english titles and abstracts from all applications with earliest_publn_year_this_family_id = this year 
        # and remove '  ' if existent

        titles_this_year = list(set(data[(data['appln_title_lg']=='en') & (data['earliest_publn_year_this_family_id']==year)]['appln_title']))
        try:
            titles_this_year.remove('  ')
        except:
            #print(str(year)+": '  ' not in titles")
            pass

        abstracts_this_year = list(set(data[(data['appln_abstract_lg']=='en') & (data['earliest_publn_year_this_family_id']==year)]['appln_abstract']))
        try:
            abstracts_this_year.remove('  ')
        except:
            #print(str(year)+": '  ' not in abstracts")
            pass

        # Get count of unique titles and abstracts
        n_titles_this_year = len(titles_this_year)
        n_abstracts_this_year = len(abstracts_this_year)

        # Add them to the lists
        titles_counts.append(n_titles_this_year)
        abstracts_counts.append(n_abstracts_this_year)


In [13]:
titles_counts = []
for year in list(titles_dict):
    titles_counts.append(len(titles_dict[year]))

print(titles_counts)


[939, 1135, 1105, 1151, 1243, 1501, 1818, 2002, 2298, 2627, 3126, 4622, 5970, 6614, 7040, 6929, 6968, 7562, 8513, 9523]


In [14]:
abstracts_counts = []
for year in list(abstracts_dict):
    abstracts_counts.append(len(abstracts_dict[year]))

print(abstracts_counts)


[975, 1164, 1132, 1191, 1288, 1566, 1955, 2147, 2480, 2808, 3376, 5152, 6757, 7463, 7936, 7733, 7830, 8438, 9677, 11016]


## Write counts in a dataframe and normalise them

In [15]:
# Read total yearly counts and add column 'normalised' 

#total_yearly_counts_df = pd.read_csv('/Users/philippmetzger/Documents/GitHub/MA_temp/03 Analysis/01 Country counts/total_yearly_counts', delimiter=';')
#total_yearly_counts_df.rename(columns = {'count': 'patent families count'}, inplace = True)

#max_patent_count = total_yearly_counts_df['patent families count'].max()
#total_yearly_counts_df['patent families count normalised'] = total_yearly_counts_df['patent families count'] / max_patent_count

total_yearly_counts_df = pd.DataFrame()

total_yearly_counts_df['titles counts'] = titles_counts
max_titles_count = total_yearly_counts_df['titles counts'].max()
total_yearly_counts_df['titles count normalised'] = total_yearly_counts_df['titles counts'] / max_titles_count


total_yearly_counts_df['abstracts counts'] = abstracts_counts
max_abstracts_count = total_yearly_counts_df['abstracts counts'].max()
total_yearly_counts_df['abstracts count normalised'] = total_yearly_counts_df['abstracts counts'] / max_abstracts_count


total_yearly_counts_df


titles counts  titles count normalised  abstracts counts  \
0             939                 0.098603               975   
1            1135                 0.119185              1164   
2            1105                 0.116035              1132   
3            1151                 0.120865              1191   
4            1243                 0.130526              1288   
5            1501                 0.157618              1566   
6            1818                 0.190906              1955   
7            2002                 0.210228              2147   
8            2298                 0.241311              2480   
9            2627                 0.275858              2808   
10           3126                 0.328258              3376   
11           4622                 0.485351              5152   
12           5970                 0.626903              6757   
13           6614                 0.694529              7463   
14           7040                 0.739263              7936   
15           6929                 0.727607              7733   
16           6968                 0.731702              7830   
17           7562                 0.794077              8438   
18           8513                 0.893941              9677   
19           9523                 1.000000             11016   

    abstracts count normalised  
0                     0.088508  
1                     0.105664  
2                     0.102760  
3                     0.108115  
4                     0.116921  
5                     0.142157  
6                     0.177469  
7                     0.194898  
8                     0.225127  
9                     0.254902  
10                    0.306463  
11                    0.467683  
12                    0.613381  
13                    0.677469  
14                    0.720407  
15                    0.701979  
16                    0.710784  
17                    0.765977  
18                    0.878450  
19                    1.000000

## Define stopwords, contexts, equivalents, words to replace, and punctuation

In [16]:
stopwords_ = stopwords.words('english')
stopwords_.extend([
    'thereof', 'therefor', 'thereafter', 'wherein', 'utmost',
    'without', 'within',
    'xo', 'e', 'etc', 'ab', 'b', 'c', 'pct', 'wo', 'pt', 'pts', 'wt', 'xii', 'xiii', 'ymyo', 'xmn', 'xiv', 'le', 'sub',
    'r', 'x', 'g', 'p', 'v', 'zfz', 'zsz',
    'positive', 'negative', 'left', 'right',
    'high', 'low',
    'less', 'les', 'more', 'least',
    'judging', 'preparing', 'producing', 'comprising', 'following', 'containing', 'including', 'using', 'consisting',
    'making',
    'one', 'two', 'never',
    'end',
    'almost', 'like', 'also',
    'especially', 'preferably', 'surely', 'nearly', 'previously', 'mainly',
    'involves', 'comprises', 'provides', 'relates', 'belongs', 'discloses', 'includes',
    'solved', 'expressed', 'specified', 'provided', 'selected', 'characterized', 'included', 'equipped',
    'decided', 'made', 'filed', 'used', 'formed', 'said',
    'provide', 'improve', 'prevent', 'obtain', 'reduce', 'enhance', 'increase', 'suppress', 'realize', 'use',
    'first', 'second',
    'simple', 'convenient',
    'whose',
    'according',
    'capable', 'preferable', 'desirable',
    'desirably',
    'kind',
    'date', 'temp', 'sec', 
    'jan', 'apr', 'may', 'jun', 'jul', 'nov', 'oct',
    'jp',
    'problem', 'drawing', 'figure', 'invention', 'model', 'publication', 'utility', 'preparation',
    'method', 'application', 'purpose', 'number',
    'new', 'novel',
    'excellent',
    'non',
    'top', 'bottom'
])


# Contexts in which first word should be kept
contexts_after = [
    ['positive', 'electrode'],
    ['negative', 'electrode'],
    ['positive', 'electrodes'],
    ['negative', 'electrodes'],
    ['positive', 'active', 'material'],
    ['negative', 'active', 'material'],
    ['non', 'aqueous'],
    ['non', 'sintered'],
    ['top', 'cap'],
    ['bottom', 'plate']
]


# Contexts in which second word should be kept
contexts_before = [
    ['lithium', 'containing']
]
    

treat_as_same = [
    [('method', 'manufacturing'), ('manufacturing', 'method')],
    [('storage', 'battery', 'alkaline'), ('alkaline', 'storage', 'battery')],
    [('battery', 'alkaline', 'storage'), ('alkaline', 'storage', 'battery')]
]


replace_words = {
    'soln': 'solution',
    'aq': 'aqueous',
    'nonaqueous': 'non aqueous',
    'obtd': 'obtained',
    'hr': 'hour',
    'pub': 'publication',
    'compsn': 'composition',
    'contg': 'containing',
    'compd': 'compound',
    'mfg': 'manufacturing',
    'methodfor': 'method for',
    'al': 'aluminium',
    'aluminum': 'aluminium',
    'co': 'cobalt',
    'mn': 'manganese',
    'ni': 'nickel',
    'zr': 'zirconium',
    'cr': 'chromium',
    'ti': 'titanium',
    'li': 'lithium',
    'la': 'lanthanum',
    'ce': 'cerium',
    'fe': 'iron',
    'ltoreq':'less than or equal',
    'deg': 'degree'
}


# This is not used in this application after all:
punctuation = '!"#$%&\()*+,-./:;<=>?@[\\]^_`{|}~'


In [17]:
# Check if replace_words dictionary works as it should

item = ['negative', 'obtd', 'soln', 'nonaqueous', 'active', 'material']

item_replaced = []
for word in item:
    
    if word in list(replace_words):
        
        item_replaced.extend(replace_words[word].split())
        
    else:
        
        item_replaced.append(word)
    
item = item_replaced
    
item


['negative', 'obtained', 'solution', 'non', 'aqueous', 'active', 'material']

## Define a function for taking care of key phrases extraction and counting

In [18]:
# Old version:

if False:
    
    def growing_keywords(n_gram_length, item_type, measure_function, normalise):

        # Initialise lemmatizer
        lem = WordNetLemmatizer()

        # create string for identifying the right language column
        item_type_lg = item_type+'_lg'

        # Initialise n grams list
        ngrams_lists = []

        # Loop over years
        for year in tqdm(years):

            # Initialise n grams list for this year
            ngrams_list_this_year = []

            # Get all  
            items_year = list(set(data[(data[item_type_lg]=='en') & (data['earliest_publn_year_this_family_id']==year)][item_type]))

            for item in items_year:

                # Make all lowercase
                item = item.lower()

                # Punctuation removal
                item = re.sub('[^a-zA-Z]', ' ', item) 
                #for x in punctuation:
                #    item = item.replace(x,' ')

                # Tokenise
                item = item.split()

                #####

                # Replace certain words with others (according to replace_words dictionary defined above)
                item_replaced = []

                for word in item:

                    if word in list(replace_words):

                        item_replaced.extend(replace_words[word].split())

                    else:

                        item_replaced.append(word)

                item = item_replaced

                #####

                # Remove stopwords; but only if they are not in a context that indicates that they should be kept.
                # Such contexts are defined in cell above (contexts_after and contexts_before).

                item_without_stopwords = []

                # For debugging: List of stopwords that will be checked
                check_list = []
                # For debugging: List of stopwords that are actually removed (because they are not in a certain context)
                remove_list = []

                for i, word in enumerate(item):

                    remove = False

                    if word in stopwords_:

                        check_list.append(word)

                        # Treat cases with context after the word or phrase

                        in_context_after = False

                        for j, context in enumerate(contexts_after):

                            if i<(len(item)-(len(context)-1)):

                                try:

                                    to_compare = []

                                    for k in range(len(context)):
                                        to_compare.append(item[i+k])

                                    if to_compare == context:
                                        in_context_after = True

                                        if False:
                                            print('not removed due to context')
                                            print(to_compare)
                                            print(context)
                                            print()

                                except:
                                    print(contexts_after)
                                    print(item)
                                    print(len(item))
                                    print(i+k)
                                    print(to_compare)
                                    print(context)

                        if not in_context_after:

                            remove = True

                        # Treat cases with context before the word or phrase

                        in_context_before = False

                        for j, context in enumerate(contexts_before):

                            if i>(len(context)-1):

                                try:

                                    to_compare = []

                                    for k in range(len(context)):

                                        to_compare.append(item[i+k-(len(context)-1)])

                                    if to_compare == context:
                                        in_context_before = True

                                        if False:
                                            print('not removed due to context')
                                            print(to_compare)
                                            print(context)
                                            print()

                                except:
                                    print(contexts_before)
                                    print(item)
                                    print(len(item))
                                    print(i+k)
                                    print(to_compare)
                                    print(context)

                        if not in_context_before:

                            remove = True

                    if not remove:

                        item_without_stopwords.append(word)

                    else:

                        remove_list.append(word)

                #####

                # Delete words that are a repetition of the word before

                # Always add the first word to next stage
                # If this list of words is empty, do nothing
                try:
                    item_without_stopwords_and_repetitions = [item_without_stopwords[0]]
                except Exception as e:
                    pass

                # Loop over the other words (the second and following) and add them to the next stage, if they are not 
                # a repetition of the word before
                for i in range(1, len(item_without_stopwords)):

                    if (item_without_stopwords[i-1] != item_without_stopwords[i]):

                        item_without_stopwords_and_repetitions.append(item_without_stopwords[i]) 

                #####

                # Lemmatisation
                item_without_stopwords_lemmatized = [lem.lemmatize(word) for word in item_without_stopwords_and_repetitions] 

                #####

                # Get ngrams
                ngrams_ = list(ngrams(item_without_stopwords_lemmatized, n_gram_length))

                # Treat certain pairs of n_grams as the same (defined in cell above (treat_as_same))
                for n_gram_treat_as_same in treat_as_same:

                    while n_gram_treat_as_same[0] in ngrams_:

                        ngrams_.remove(n_gram_treat_as_same[0])
                        ngrams_.append(n_gram_treat_as_same[1])

                # Add to list
                ngrams_list_this_year.extend(ngrams_)

            ngrams_lists.append(ngrams_list_this_year)

        print('n grams created')

        #####

        # Count n grams' appearances
        counter_list = []
        unique_keys = set()

        for list_ in ngrams_lists:

            counter = dict(Counter(list_).most_common())
            counter_list.append(counter)

            unique_keys = unique_keys.union(set(counter.keys()))

        #####

        # Create a count entry of 0 for n grams that appeared in at least one year but not in others
        for counter in counter_list:

            for key_ in unique_keys:

                if key_ not in counter:

                    counter[key_] = 0

        #####

        # NEW 10 Nov 2021: Increment all counts by 1 (in order to avoid division by 0 in growth calculation)
        # This is only necessary when using relative growth (see growth calcuation further down)
        if False:

            for counter in counter_list:

                for key_ in counter:

                        counter[key_] = counter[key_] + 1

        #####

        # NEW 10 Nov 2021: Normalise by year's distinct title / abstract count

        if normalise:

            if item_type == 'appln_title':
                normalised_patent_counts = list(total_yearly_counts_df['titles count normalised'])

            elif item_type == 'appln_abstract':
                normalised_patent_counts = list(total_yearly_counts_df['abstracts count normalised'])

            else:
                print('Item type not recognised')
                return

            for i, counter in enumerate(counter_list):

                normalised_patent_count_this_year = normalised_patent_counts[i]

                for key_ in counter:

                    value_scaled = counter[key_] / normalised_patent_count_this_year
                    counter[key_] = value_scaled

        #####

        # Calculate growth
        # NEW 10 Nov 2021: Added alternative growth calculation growth = (x1 - x0)/x0
        # NEW 13 Nov 2021: Added alternative growth calculation growth = abs(x1 - x0)
        growth_dict = {}
        growth_dict_absolute = {}

        for key_ in unique_keys:

            try:
                growth = []
                for i in range(len(counter_list)-1):

                    # Growing and shrinking not treated as the same.
                    # Growth as (x1 - x0)
                    growth.append(counter_list[i+1][key_]-counter_list[i][key_])

                    # Growth as (x1 - x0)/x0
                    #growth.append((counter_list[i+1][key_] - counter_list[i][key_]) / counter_list[i][key_])

            except:
                print('Not possible with key:', key_)

            m_growth = measure_function(growth)

            growth_dict[key_] = m_growth

        print('growth calculated')

        for key_ in unique_keys:

            try:
                growth = []
                for i in range(len(counter_list)-1):

                    # Absolute growth (growing and shrinking are treated as the same)
                    growth.append(abs(counter_list[i+1][key_]-counter_list[i][key_]))

            except:
                print('Absolute growth - Not possible with key:', key_)

            m_growth = measure_function(growth)

            growth_dict_absolute[key_] = m_growth

        print('absolute growth calculated')

        #####
        #####

        # Prepare positive growth plot
        highest_growth = dict(sorted(growth_dict.items(), key=lambda x:x[1], reverse=True))
        top_30_growth = list(highest_growth)[:30]
        top_50_growth = list(highest_growth)[:50]

        growing_list = []
        growing_list.append(top_50_growth)

        #####

        counts_list = []

        #for key_ in top_30_growth:
        for key_ in top_50_growth:

            counts = []

            for counter in counter_list:

                counts.append(counter[key_])

            counts_list.append(counts)

        #####

        df_keyword_growth = pd.DataFrame(index=years)
        for i, ngram_ in enumerate(top_50_growth):

            ngram_string = ' '.join(ngram_)

            df_keyword_growth[ngram_string] = counts_list[i]

        df_keyword_growth = df_keyword_growth.transpose()

        # Round all values
        df_keyword_growth = df_keyword_growth.round()
        df_keyword_growth = df_keyword_growth.apply(pd.to_numeric, downcast='integer')

        growing_list.append(df_keyword_growth)

        #####

        cm = sns.light_palette((260, 75, 60), input="husl", as_cmap=True)

        plot_positive_growth = df_keyword_growth.style.background_gradient(cmap=cm, axis=1)

        growing_list.append(plot_positive_growth)

        print('positive growth plot created')

        #####
        #####

        # Prepare negative growth plot

        highest_growth = dict(sorted(growth_dict.items(), key=lambda x:x[1], reverse=False))
        top_30_growth = list(highest_growth)[:30]
        top_50_growth = list(highest_growth)[:50]

        shrinking_list = []
        shrinking_list.append(top_50_growth)

        #####

        counts_list = []

        for key_ in top_50_growth:

            counts = []

            for counter in counter_list:

                counts.append(counter[key_])

            counts_list.append(counts)

        #####

        df_keyword_growth = pd.DataFrame(index=years)
        for i, ngram_ in enumerate(top_50_growth):

            ngram_string = ' '.join(ngram_)

            df_keyword_growth[ngram_string] = counts_list[i]

        df_keyword_growth = df_keyword_growth.transpose()

        # Round all values
        df_keyword_growth = df_keyword_growth.round()
        df_keyword_growth = df_keyword_growth.apply(pd.to_numeric, downcast='integer')

        shrinking_list.append(df_keyword_growth)

        #####

        cm = sns.light_palette((260, 75, 60), input="husl", as_cmap=True)

        plot_negative_growth = df_keyword_growth.style.background_gradient(cmap=cm, axis=1)

        shrinking_list.append(plot_negative_growth)

        print('negative growth plot created')

        #####
        #####

        # Prepare absolute growth plot
        highest_growth = dict(sorted(growth_dict_absolute.items(), key=lambda x:x[1], reverse=True))
        top_30_growth = list(highest_growth)[:30]
        top_50_growth = list(highest_growth)[:50]

        absolute_growth_list = []
        absolute_growth_list.append(top_50_growth)

        #####

        counts_list = []

        #for key_ in top_30_growth:
        for key_ in top_50_growth:

            counts = []

            for counter in counter_list:

                counts.append(counter[key_])

            counts_list.append(counts)

        #####

        df_keyword_growth = pd.DataFrame(index=years)
        for i, ngram_ in enumerate(top_50_growth):

            ngram_string = ' '.join(ngram_)

            df_keyword_growth[ngram_string] = counts_list[i]

        df_keyword_growth = df_keyword_growth.transpose()

        # Round all values
        df_keyword_growth = df_keyword_growth.round()
        df_keyword_growth = df_keyword_growth.apply(pd.to_numeric, downcast='integer')

        absolute_growth_list.append(df_keyword_growth)

        #####

        cm = sns.light_palette((260, 75, 60), input="husl", as_cmap=True)

        plot_absolute_growth = df_keyword_growth.style.background_gradient(cmap=cm, axis=1)

        absolute_growth_list.append(plot_absolute_growth)

        print('absolute growth plot created')

        return growing_list, shrinking_list, absolute_growth_list
    

In [19]:
# Version 17 Jan 2022

if False:
    
    def growing_keywords(n_gram_length, item_type, measure_function, normalise):

        # Initialise lemmatizer
        lem = WordNetLemmatizer()

        # create string for identifying the right language column
        #item_type_lg = item_type+'_lg'

        # Initialise n grams list
        ngrams_lists = []

        # Loop over years
        for year in tqdm(years):

            # Initialise n grams list for this year
            ngrams_list_this_year = []

            # Get all  
            #items_year = list(set(data[(data[item_type_lg]=='en') & (data['earliest_publn_year_this_family_id']==year)][item_type]))

            # Get this year's titles / abstracts (depending which mode we're in)
            if item_type == 'appln_title':
                items_year = list(titles_dict[year])
            if item_type == 'appln_abstract':
                items_year = list(abstracts_dict[year])

            for item in items_year:

                # Make all lowercase
                item = item.lower()

                # Punctuation removal
                item = re.sub('[^a-zA-Z]', ' ', item) 
                #for x in punctuation:
                #    item = item.replace(x,' ')

                # Tokenise
                item = item.split()

                #####

                # Replace certain words with others (according to replace_words dictionary defined above)
                item_replaced = []

                for word in item:

                    if word in list(replace_words):

                        item_replaced.extend(replace_words[word].split())

                    else:

                        item_replaced.append(word)

                item = item_replaced

                #####

                # Remove stopwords; but only if they are not in a context that indicates that they should be kept.
                # Such contexts are defined in cell above (contexts_after and contexts_before).

                item_without_stopwords = []

                # For debugging: List of stopwords that will be checked
                check_list = []
                # For debugging: List of stopwords that are actually removed (because they are not in a certain context)
                remove_list = []

                for i, word in enumerate(item):

                    remove = False

                    if word in stopwords_:

                        check_list.append(word)

                        # Treat cases with context after the word or phrase

                        in_context_after = False

                        for j, context in enumerate(contexts_after):

                            if i<(len(item)-(len(context)-1)):

                                try:

                                    to_compare = []

                                    for k in range(len(context)):
                                        to_compare.append(item[i+k])

                                    if to_compare == context:
                                        in_context_after = True

                                        if False:
                                            print('not removed due to context')
                                            print(to_compare)
                                            print(context)
                                            print()

                                except:
                                    print(contexts_after)
                                    print(item)
                                    print(len(item))
                                    print(i+k)
                                    print(to_compare)
                                    print(context)

                        if not in_context_after:

                            remove = True

                        # Treat cases with context before the word or phrase

                        in_context_before = False

                        for j, context in enumerate(contexts_before):

                            if i>(len(context)-1):

                                try:

                                    to_compare = []

                                    for k in range(len(context)):

                                        to_compare.append(item[i+k-(len(context)-1)])

                                    if to_compare == context:
                                        in_context_before = True

                                        if False:
                                            print('not removed due to context')
                                            print(to_compare)
                                            print(context)
                                            print()

                                except:
                                    print(contexts_before)
                                    print(item)
                                    print(len(item))
                                    print(i+k)
                                    print(to_compare)
                                    print(context)

                        if not in_context_before:

                            remove = True

                    if not remove:

                        item_without_stopwords.append(word)

                    else:

                        remove_list.append(word)

                #####

                # Delete words that are a repetition of the word before

                # Always add the first word to next stage
                # If this list of words is empty, do nothing
                try:
                    item_without_stopwords_and_repetitions = [item_without_stopwords[0]]
                except Exception as e:
                    pass

                # Loop over the other words (the second and following) and add them to the next stage, if they are not 
                # a repetition of the word before
                for i in range(1, len(item_without_stopwords)):

                    if (item_without_stopwords[i-1] != item_without_stopwords[i]):

                        item_without_stopwords_and_repetitions.append(item_without_stopwords[i]) 

                #####

                # Lemmatisation
                item_without_stopwords_lemmatized = [lem.lemmatize(word) for word in item_without_stopwords_and_repetitions] 

                #####

                # Get ngrams
                ngrams_ = list(ngrams(item_without_stopwords_lemmatized, n_gram_length))

                # Treat certain pairs of n_grams as the same (defined in cell above (treat_as_same))
                for n_gram_treat_as_same in treat_as_same:

                    while n_gram_treat_as_same[0] in ngrams_:

                        ngrams_.remove(n_gram_treat_as_same[0])
                        ngrams_.append(n_gram_treat_as_same[1])

                # Add to list
                ngrams_list_this_year.extend(ngrams_)

            ngrams_lists.append(ngrams_list_this_year)

        print('n grams created')

        #####

        # Count n grams' appearances
        counter_list = []
        unique_keys = set()

        for list_ in ngrams_lists:

            counter = dict(Counter(list_).most_common())
            counter_list.append(counter)

            unique_keys = unique_keys.union(set(counter.keys()))

        #####

        # NEW 17 Jan 2022: Delete all phrases that have at least one year where the counter is zero.
        # V2, same day: Delete all phrases that have more than 15 years where the counter is zero.

        unique_keys_reduced = set()

        for key_ in unique_keys:

            has_zero = 0

            for counter in counter_list:

                if key_ not in counter:

                    has_zero += 1

            if has_zero > 15:

                for counter in counter_list:

                    try:
                        counter.pop(key_)
                    except Exception as pop_error:
                        pass
                        #print(type(pop_error))
                        #print(pop_error)
                        #print()

            else:

                unique_keys_reduced.add(key_)

        unique_keys = unique_keys_reduced

        #####

        # Create a count entry of 0 for n grams that is present in at least one year but not in other(s)
        for counter in counter_list:

            for key_ in unique_keys:

                if key_ not in counter:

                    counter[key_] = 0

        #####      

        relative = True

        # NEW 10 Nov 2021: Increment all counts by 1 (in order to avoid division by 0 in growth calculation)
        # This is only necessary when using relative growth (see growth calcuation further down)
        if relative:

            for counter in counter_list:

                for key_ in counter:

                        counter[key_] = counter[key_] + 1

        #####

        # NEW 10 Nov 2021: Normalise by year's distinct title / abstract count

        if normalise:

            if item_type == 'appln_title':
                normalised_patent_counts = list(total_yearly_counts_df['titles count normalised'])

            elif item_type == 'appln_abstract':
                normalised_patent_counts = list(total_yearly_counts_df['abstracts count normalised'])

            else:
                print('Item type not recognised')
                return

            for i, counter in enumerate(counter_list):

                normalised_patent_count_this_year = normalised_patent_counts[i]

                for key_ in counter:

                    value_scaled = counter[key_] / normalised_patent_count_this_year
                    counter[key_] = value_scaled

        #####

        # Calculate growth
        # Growing and shrinking not treated as the same.
        # NEW 10 Nov 2021: Added alternative growth calculation growth = (x1 - x0)/x0
        # NEW 13 Nov 2021: Added alternative growth calculation growth = abs(x1 - x0)
        growth_dict = {}
        growth_dict_absolute = {}

        for key_ in unique_keys:

            growth = []
            for i in range(len(counter_list)-1):

                if not relative:

                    # Growth as (x1 - x0)
                    growth.append(counter_list[i+1][key_]-counter_list[i][key_])

                else:

                    # Growth as (x1 - x0)/x0. Only works if x0 is not zero.
                    try:
                        growth.append((counter_list[i+1][key_] / counter_list[i][key_]) - 1)
                    except:
                        print('error')
                    #    pass
                        #print(counter_list[i][key_])

            try:
                m_growth = measure_function(growth)
            except Exception as e1:
                print(type(e1))
                print(e1)

            growth_dict[key_] = m_growth

        print('growth calculated')

        # Absolute growth
        # Growing and shrinking are treated as the same
        for key_ in unique_keys:

            growth = []
            for i in range(len(counter_list)-1):

                if not relative:

                    # Growth as abs(x1 - x0)
                    growth.append(abs(counter_list[i+1][key_]-counter_list[i][key_]))

                else:

                    # Growth as abs(x1 - x0)/x0. Only works if x0 is not zero.
                    try:
                        growth.append(abs(counter_list[i+1][key_] / counter_list[i][key_]) - 1)
                    except:
                        print('error')
                    #    pass
                        #print(counter_list[i][key_])

            try:
                m_growth = measure_function(growth)
            except Exception as e2:
                print(type(e2))
                print(e2)

            growth_dict_absolute[key_] = m_growth

        print('absolute growth calculated')

        #####
        #####

        # Prepare positive growth plot
        highest_growth = dict(sorted(growth_dict.items(), key=lambda x:x[1], reverse=True))
        top_30_growth = list(highest_growth)[:30]
        top_50_growth = list(highest_growth)[:50]

        growing_list = []
        growing_list.append(top_50_growth)

        #####

        counts_list = []

        #for key_ in top_30_growth:
        for key_ in top_50_growth:

            counts = []

            for counter in counter_list:

                counts.append(counter[key_])

            counts_list.append(counts)

        #####

        df_keyword_growth = pd.DataFrame(index=years)
        for i, ngram_ in enumerate(top_50_growth):

            ngram_string = ' '.join(ngram_)

            df_keyword_growth[ngram_string] = counts_list[i]

        df_keyword_growth = df_keyword_growth.transpose()

        # Round all values
        df_keyword_growth = df_keyword_growth.round()
        df_keyword_growth = df_keyword_growth.apply(pd.to_numeric, downcast='integer')

        growing_list.append(df_keyword_growth)

        #####

        cm = sns.light_palette((260, 75, 60), input="husl", as_cmap=True)

        plot_positive_growth = df_keyword_growth.style.background_gradient(cmap=cm, axis=1)

        growing_list.append(plot_positive_growth)

        print('positive growth plot created')

        #####
        #####

        # Prepare negative growth plot

        highest_growth = dict(sorted(growth_dict.items(), key=lambda x:x[1], reverse=False))
        top_30_growth = list(highest_growth)[:30]
        top_50_growth = list(highest_growth)[:50]

        shrinking_list = []
        shrinking_list.append(top_50_growth)

        #####

        counts_list = []

        for key_ in top_50_growth:

            counts = []

            for counter in counter_list:

                counts.append(counter[key_])

            counts_list.append(counts)

        #####

        df_keyword_growth = pd.DataFrame(index=years)
        for i, ngram_ in enumerate(top_50_growth):

            ngram_string = ' '.join(ngram_)

            df_keyword_growth[ngram_string] = counts_list[i]

        df_keyword_growth = df_keyword_growth.transpose()

        # Round all values
        df_keyword_growth = df_keyword_growth.round()
        df_keyword_growth = df_keyword_growth.apply(pd.to_numeric, downcast='integer')

        shrinking_list.append(df_keyword_growth)

        #####

        cm = sns.light_palette((260, 75, 60), input="husl", as_cmap=True)

        plot_negative_growth = df_keyword_growth.style.background_gradient(cmap=cm, axis=1)

        shrinking_list.append(plot_negative_growth)

        print('negative growth plot created')

        #####
        #####

        # Prepare absolute growth plot
        highest_growth = dict(sorted(growth_dict_absolute.items(), key=lambda x:x[1], reverse=True))
        top_30_growth = list(highest_growth)[:30]
        top_50_growth = list(highest_growth)[:50]

        absolute_growth_list = []
        absolute_growth_list.append(top_50_growth)

        #####

        counts_list = []

        #for key_ in top_30_growth:
        for key_ in top_50_growth:

            counts = []

            for counter in counter_list:

                counts.append(counter[key_])

            counts_list.append(counts)

        #####

        df_keyword_growth = pd.DataFrame(index=years)
        for i, ngram_ in enumerate(top_50_growth):

            ngram_string = ' '.join(ngram_)

            df_keyword_growth[ngram_string] = counts_list[i]

        df_keyword_growth = df_keyword_growth.transpose()

        # Round all values
        df_keyword_growth = df_keyword_growth.round()
        df_keyword_growth = df_keyword_growth.apply(pd.to_numeric, downcast='integer')

        absolute_growth_list.append(df_keyword_growth)

        #####

        cm = sns.light_palette((260, 75, 60), input="husl", as_cmap=True)

        plot_absolute_growth = df_keyword_growth.style.background_gradient(cmap=cm, axis=1)

        absolute_growth_list.append(plot_absolute_growth)

        print('absolute growth plot created')

        return growing_list, shrinking_list, absolute_growth_list


In [20]:
def growing_keywords(n_gram_length, item_type):
    
    # Initialise lemmatizer
    lem = WordNetLemmatizer()
    
    # create string for identifying the right language column
    #item_type_lg = item_type+'_lg'
    
    # Initialise n grams list
    ngrams_lists = []

    # Loop over years
    for year in tqdm(years):

        # Initialise n grams list for this year
        ngrams_list_this_year = []

        # Get all  
        #items_year = list(set(data[(data[item_type_lg]=='en') & (data['earliest_publn_year_this_family_id']==year)][item_type]))
        
        # Get this year's titles / abstracts (depending which mode we're in)
        if item_type == 'appln_title':
            items_year = list(titles_dict[year])
        if item_type == 'appln_abstract':
            items_year = list(abstracts_dict[year])
                
        for item in items_year:
            
            # Make all lowercase
            item = item.lower()

            # Punctuation removal
            item = re.sub('[^a-zA-Z]', ' ', item) 
            #for x in punctuation:
            #    item = item.replace(x,' ')

            # Tokenise
            item = item.split()
            
            #####
            
            # Replace certain words with others (according to replace_words dictionary defined above)
            item_replaced = []
            
            for word in item:

                if word in list(replace_words):
        
                    item_replaced.extend(replace_words[word].split())

                else:

                    item_replaced.append(word)

            item = item_replaced
            
            #####
            
            # Remove stopwords; but only if they are not in a context that indicates that they should be kept.
            # Such contexts are defined in cell above (contexts_after and contexts_before).
            
            item_without_stopwords = []

            # For debugging: List of stopwords that will be checked
            check_list = []
            # For debugging: List of stopwords that are actually removed (because they are not in a certain context)
            remove_list = []
                        
            for i, word in enumerate(item):
                
                remove = False

                if word in stopwords_:
 
                    check_list.append(word)

                    # Treat cases with context after the word or phrase
        
                    in_context_after = False

                    for j, context in enumerate(contexts_after):
                        
                        if i<(len(item)-(len(context)-1)):

                            try:

                                to_compare = []
                                
                                for k in range(len(context)):
                                    to_compare.append(item[i+k])
                                    
                                if to_compare == context:
                                    in_context_after = True
                                    
                                    if False:
                                        print('not removed due to context')
                                        print(to_compare)
                                        print(context)
                                        print()

                            except:
                                print(contexts_after)
                                print(item)
                                print(len(item))
                                print(i+k)
                                print(to_compare)
                                print(context)

                    if not in_context_after:

                        remove = True
                        
                    # Treat cases with context before the word or phrase
        
                    in_context_before = False

                    for j, context in enumerate(contexts_before):
                        
                        if i>(len(context)-1):
                                
                            try:

                                to_compare = []

                                for k in range(len(context)):
                                    
                                    to_compare.append(item[i+k-(len(context)-1)])

                                if to_compare == context:
                                    in_context_before = True
                                    
                                    if False:
                                        print('not removed due to context')
                                        print(to_compare)
                                        print(context)
                                        print()

                            except:
                                print(contexts_before)
                                print(item)
                                print(len(item))
                                print(i+k)
                                print(to_compare)
                                print(context)

                    if not in_context_before:

                        remove = True
                        
                if not remove:
                    
                    item_without_stopwords.append(word)
                    
                else:
                                            
                    remove_list.append(word)

            #####
            
            # Delete words that are a repetition of the word before
            
            # Always add the first word to next stage
            # If this list of words is empty, do nothing
            try:
                item_without_stopwords_and_repetitions = [item_without_stopwords[0]]
            except Exception as e:
                pass
                                    
            # Loop over the other words (the second and following) and add them to the next stage, if they are not 
            # a repetition of the word before
            for i in range(1, len(item_without_stopwords)):
                
                if (item_without_stopwords[i-1] != item_without_stopwords[i]):
                    
                    item_without_stopwords_and_repetitions.append(item_without_stopwords[i]) 
            
            #####
            
            # Lemmatisation
            item_without_stopwords_lemmatized = [lem.lemmatize(word) for word in item_without_stopwords_and_repetitions] 

            #####
            
            # Get ngrams
            ngrams_ = list(ngrams(item_without_stopwords_lemmatized, n_gram_length))
            
            # Treat certain pairs of n_grams as the same (defined in cell above (treat_as_same))
            for n_gram_treat_as_same in treat_as_same:
                
                while n_gram_treat_as_same[0] in ngrams_:
                    
                    ngrams_.remove(n_gram_treat_as_same[0])
                    ngrams_.append(n_gram_treat_as_same[1])

            # Add to list
            ngrams_list_this_year.extend(ngrams_)
            
        # For 3-grams: delete it if first word is equal to third word, e.g. battery pack battery
        if n_gram_length == 3:
            
            ngrams_list_this_year_reduced = []
            
            for item in ngrams_list_this_year:
                
                if not item[0] == item[2]:
                    
                    ngrams_list_this_year_reduced.append(item)
                    
            ngrams_list_this_year = ngrams_list_this_year_reduced

        ngrams_lists.append(ngrams_list_this_year)
        
    print('N-grams created')

    #####
    
    # Count n grams' appearances
    counter_list = []
    unique_keys = set()

    for list_ in ngrams_lists:

        counter = dict(Counter(list_).most_common())
        counter_list.append(counter)

        unique_keys = unique_keys.union(set(counter.keys()))
        
    print('N-grams counted')

    #####
    
    # NEW 17 Jan 2022: Delete all phrases that have at least one year where the counter is zero.
    # V2, same day: Delete all phrases that have more than 15 years where the counter is zero.
    if False:
        
        unique_keys_reduced = set()

        for key_ in unique_keys:

            has_zero = 0

            for counter in counter_list:

                if key_ not in counter:

                    has_zero += 1

            if has_zero > 15:

                for counter in counter_list:

                    try:
                        counter.pop(key_)
                    except Exception as pop_error:
                        pass
                        #print(type(pop_error))
                        #print(pop_error)
                        #print()

            else:

                unique_keys_reduced.add(key_)

        unique_keys = unique_keys_reduced
                
    #####
    
    # Create a count entry of 0 for n grams that is present in at least one year but not in other(s)
    for counter in counter_list:

        for key_ in unique_keys:

            if key_ not in counter:

                counter[key_] = 0

    #####      
    
    relative = False
    
    # NEW 10 Nov 2021: Increment all counts by 1 (in order to avoid division by 0 in growth calculation)
    # This is only necessary when using relative growth (see growth calcuation further down)
    if relative:
        
        for counter in counter_list:

            for key_ in counter:

                    counter[key_] = counter[key_] + 1
    
    def growing_keywords_sub(counter_list, unique_keys, scale):
    
        #####

        # NEW 10 Nov 2021: Scale by year's distinct title / abstract count
        # NEW 18 Jan 2022: Scale by year's distinct title / abstract count to make it "per 1000 titles / abstracts"

        if scale:

            if item_type == 'appln_title':
                #normalised_patent_counts = list(total_yearly_counts_df['titles count normalised'])
                patent_counts = list(total_yearly_counts_df['titles counts'])

            elif item_type == 'appln_abstract':
                #normalised_patent_counts = list(total_yearly_counts_df['abstracts count normalised'])
                patent_counts = list(total_yearly_counts_df['abstracts counts'])

            else:
                print('Item type not recognised')
                return

            for i, counter in enumerate(counter_list):

                #normalised_patent_count_this_year = normalised_patent_counts[i]
                patent_count_this_year = patent_counts[i]

                for key_ in counter:

                    #value_scaled = counter[key_] / normalised_patent_count_this_year
                    value_scaled = counter[key_] / patent_count_this_year * 1000
                    counter[key_] = value_scaled


        #####

        # Calculate increase over whole time span
        growth_dict = {}
        growth_dict_absolute = {}

        for key_ in unique_keys:

            growth_dict[key_] = counter_list[len(counter_list) - 1][key_] - counter_list[0][key_]

        print('Difference over whole timespan calculated')

        # Calculate sum of absolute differences year-over-year; absolute => Growing and shrinking are treated as the same
        for key_ in unique_keys:

            growth = []
            for i in range(len(counter_list)-1):

                if not relative:

                    # Growth as abs(x1 - x0)
                    growth.append(abs(counter_list[i+1][key_]-counter_list[i][key_]))

                else:

                    # Growth as abs(x1 / x0) - 1. Only works if x0 is not zero.
                    try:
                        growth.append(abs((counter_list[i+1][key_] / counter_list[i][key_]) - 1))
                    except:
                        print('error')

            try:
                growth_dict_absolute[key_] = sum(growth)
            except Exception as e2:
                print(type(e2))
                print(e2)

        print('Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated')

        #####
        #####

        # Prepare positive growth plot
        highest_growth = dict(sorted(growth_dict.items(), key=lambda x:x[1], reverse=True))
        top_30_growth = list(highest_growth)[:30]
        top_50_growth = list(highest_growth)[:50]

        growing_list = []
        growing_list.append(top_50_growth)

        #####

        counts_list = []

        #for key_ in top_30_growth:
        for key_ in top_50_growth:

            counts = []

            for counter in counter_list:

                counts.append(counter[key_])

            counts_list.append(counts)

        #####

        df_keyword_growth = pd.DataFrame(index=years)
        for i, ngram_ in enumerate(top_50_growth):

            ngram_string = ' '.join(ngram_)

            df_keyword_growth[ngram_string] = counts_list[i]

        df_keyword_growth = df_keyword_growth.transpose()

        # Round all values
        df_keyword_growth = df_keyword_growth.round()
        df_keyword_growth = df_keyword_growth.apply(pd.to_numeric, downcast='integer')
        
        growing_list.append(df_keyword_growth)

        #####

        cm = sns.light_palette((260, 75, 60), input="husl", as_cmap=True)

        plot_positive_growth = df_keyword_growth.style.background_gradient(cmap=cm, axis=1)
        
        # Display thousands with comma separation
        plot_positive_growth.format("{:,d}")

        growing_list.append(plot_positive_growth)

        print('Positive change plot created')

        #####
        #####

        # Prepare negative growth plot

        highest_growth = dict(sorted(growth_dict.items(), key=lambda x:x[1], reverse=False))
        top_30_growth = list(highest_growth)[:30]
        top_50_growth = list(highest_growth)[:50]

        shrinking_list = []
        shrinking_list.append(top_50_growth)

        #####

        counts_list = []

        for key_ in top_50_growth:

            counts = []

            for counter in counter_list:

                counts.append(counter[key_])

            counts_list.append(counts)

        #####

        df_keyword_growth = pd.DataFrame(index=years)
        for i, ngram_ in enumerate(top_50_growth):

            ngram_string = ' '.join(ngram_)

            df_keyword_growth[ngram_string] = counts_list[i]

        df_keyword_growth = df_keyword_growth.transpose()

        # Round all values
        df_keyword_growth = df_keyword_growth.round()
        df_keyword_growth = df_keyword_growth.apply(pd.to_numeric, downcast='integer')

        shrinking_list.append(df_keyword_growth)

        #####

        cm = sns.light_palette((260, 75, 60), input="husl", as_cmap=True)

        plot_negative_growth = df_keyword_growth.style.background_gradient(cmap=cm, axis=1)
        
        # Display thousands with comma separation
        plot_negative_growth.format("{:,d}")

        shrinking_list.append(plot_negative_growth)

        print('Negative change plot created')

        #####
        #####

        # Prepare absolute growth plot
        highest_growth = dict(sorted(growth_dict_absolute.items(), key=lambda x:x[1], reverse=True))
        top_30_growth = list(highest_growth)[:30]
        top_50_growth = list(highest_growth)[:50]

        absolute_growth_list = []
        absolute_growth_list.append(top_50_growth)

        #####

        counts_list = []

        #for key_ in top_30_growth:
        for key_ in top_50_growth:

            counts = []

            for counter in counter_list:

                counts.append(counter[key_])

            counts_list.append(counts)

        #####

        df_keyword_growth = pd.DataFrame(index=years)
        for i, ngram_ in enumerate(top_50_growth):

            ngram_string = ' '.join(ngram_)

            df_keyword_growth[ngram_string] = counts_list[i]

        df_keyword_growth = df_keyword_growth.transpose()

        # Round all values
        df_keyword_growth = df_keyword_growth.round()
        df_keyword_growth = df_keyword_growth.apply(pd.to_numeric, downcast='integer')

        absolute_growth_list.append(df_keyword_growth)        
        
        #####

        cm = sns.light_palette((260, 75, 60), input="husl", as_cmap=True)
        
        plot_absolute_growth = df_keyword_growth.style.background_gradient(cmap=cm, axis=1)
        
        # Display thousands with comma separation
        plot_absolute_growth.format("{:,d}")

        absolute_growth_list.append(plot_absolute_growth)

        print('Absolute change plot created')

        return growing_list, shrinking_list, absolute_growth_list
    
    growing_list, shrinking_list, absolute_growth_list = growing_keywords_sub(counter_list, unique_keys, False)
    growing_list_scaled, shrinking_list_scaled, absolute_growth_list_scaled = growing_keywords_sub(counter_list, unique_keys, True)
    
    return growing_list, shrinking_list, absolute_growth_list, growing_list_scaled, shrinking_list_scaled, absolute_growth_list_scaled


# Notes
Not good:
- any zeros: delete, relative growth, mean
- any zeros: delete, relative growth, median
- any zeros: delete, normal growth, median

A bit better (shrinking only works with normalisation):
- any zeros: delete, normal growth, mean

Alright:
- \>15 zeros: delete, normal growth, mean (this is what is displayed right now)

Decision:
- Keep everything (don't delete any n-grams that have zero counts)
- Use count_last - count_first for positive and negative change and sum(abs(count_i+1 - count_i)) for absolute change
- Mean / median are not relevant anymore.
- Don't use relative growth


## Two more definitions

In [21]:
# Define whether to use median or mean
#measure_function = stat.mean
#measure_function = stat.mean


# Results

## Titles

### Titles - unigrams

In [22]:
growing_list_title_1, shrinking_list_title_1, highest_abs_change_list_title_1, growing_list_title_1_scaled, shrinking_list_title_1_scaled, highest_abs_change_list_title_1_scaled = growing_keywords(
    1,
    'appln_title'
)


  0%|          | 0/20 [00:00<?, ?it/s]

N-grams created
N-grams counted
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created


In [23]:
growing_list_title_1[2]


In [24]:
growing_list_title_1_scaled[2]


In [25]:
shrinking_list_title_1[2]


In [26]:
shrinking_list_title_1_scaled[2]


In [27]:
highest_abs_change_list_title_1[2]


In [28]:
highest_abs_change_list_title_1_scaled[2]

### Titles - bigrams

In [29]:
growing_list_title_2, shrinking_list_title_2, highest_abs_change_list_title_2, growing_list_title_2_scaled, shrinking_list_title_2_scaled, highest_abs_change_list_title_2_scaled = growing_keywords(
    2,
    'appln_title'
)


  0%|          | 0/20 [00:00<?, ?it/s]

N-grams created
N-grams counted
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created


In [30]:
growing_list_title_2[2]


In [31]:
growing_list_title_2_scaled[2]


In [32]:
shrinking_list_title_2[2]


In [33]:
shrinking_list_title_2_scaled[2]

In [34]:
highest_abs_change_list_title_2[2]

In [35]:
highest_abs_change_list_title_2_scaled[2]

### Titles - trigrams

In [36]:
growing_list_title_3, shrinking_list_title_3, highest_abs_change_list_title_3, growing_list_title_3_scaled, shrinking_list_title_3_scaled, highest_abs_change_list_title_3_scaled = growing_keywords(
    3,
    'appln_title'
)


  0%|          | 0/20 [00:00<?, ?it/s]

N-grams created
N-grams counted
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created


In [37]:
growing_list_title_3[2]


In [38]:
growing_list_title_3_scaled[2]


In [39]:
shrinking_list_title_3[2]


In [40]:
shrinking_list_title_3_scaled[2]


In [41]:
highest_abs_change_list_title_3[2]


In [42]:
highest_abs_change_list_title_3_scaled[2]


## Abstracts

### Abstracts - unigrams

In [43]:
growing_list_abstract_1, shrinking_list_abstract_1, highest_abs_change_list_abstract_1, growing_list_abstract_1_scaled, shrinking_list_abstract_1_scaled, highest_abs_change_list_abstract_1_scaled = growing_keywords(
    1,
    'appln_abstract'
)


  0%|          | 0/20 [00:00<?, ?it/s]

N-grams created
N-grams counted
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created


In [44]:
growing_list_abstract_1[2]


In [45]:
growing_list_abstract_1_scaled[2]

In [46]:
shrinking_list_abstract_1[2]


In [47]:
shrinking_list_abstract_1_scaled[2]


In [48]:
highest_abs_change_list_abstract_1[2]


In [49]:
highest_abs_change_list_abstract_1_scaled[2]


### Abstracts - bigrams

In [50]:
growing_list_abstract_2, shrinking_list_abstract_2, highest_abs_change_list_abstract_2, growing_list_abstract_2_scaled, shrinking_list_abstract_2_scaled, highest_abs_change_list_abstract_2_scaled = growing_keywords(
    2,
    'appln_abstract'
)


  0%|          | 0/20 [00:00<?, ?it/s]

N-grams created
N-grams counted
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created


In [51]:
growing_list_abstract_2[2]


In [52]:
growing_list_abstract_2_scaled[2]

In [53]:
shrinking_list_abstract_2[2]


In [54]:
shrinking_list_abstract_2_scaled[2]


In [55]:
highest_abs_change_list_abstract_2[2]


In [56]:
highest_abs_change_list_abstract_2_scaled[2]


### Abstracts - trigrams

In [57]:
growing_list_abstract_3, shrinking_list_abstract_3, highest_abs_change_list_abstract_3, growing_list_abstract_3_scaled, shrinking_list_abstract_3_scaled, highest_abs_change_list_abstract_3_scaled = growing_keywords(
    3,
    'appln_abstract'
)


  0%|          | 0/20 [00:00<?, ?it/s]

N-grams created
N-grams counted
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created


In [58]:
growing_list_abstract_3[2]


In [59]:
dfi.export(growing_list_abstract_3[2], 'growing_list_abstract_3.png')


[0118/155241.869859:ERROR:xattr.cc(63)] setxattr org.chromium.crashpad.database.initialized on file /var/folders/c3/ddgk3fbs6w1gm4pg4tfj0d0r0000gn/T/: Operation not permitted (1)
[0118/155241.873678:ERROR:file_io.cc(94)] ReadExactly: expected 8, observed 0
[0118/155241.877645:ERROR:xattr.cc(63)] setxattr org.chromium.crashpad.database.initialized on file /var/folders/c3/ddgk3fbs6w1gm4pg4tfj0d0r0000gn/T/: Operation not permitted (1)
[0118/155243.159463:INFO:headless_shell.cc(653)] Written to file /var/folders/c3/ddgk3fbs6w1gm4pg4tfj0d0r0000gn/T/tmpnfqin542/temp.png.
[0118/155243.524191:ERROR:xattr.cc(63)] setxattr org.chromium.crashpad.database.initialized on file /var/folders/c3/ddgk3fbs6w1gm4pg4tfj0d0r0000gn/T/: Operation not permitted (1)
[0118/155243.527576:ERROR:file_io.cc(94)] ReadExactly: expected 8, observed 0
[0118/155243.530803:ERROR:xattr.cc(63)] setxattr org.chromium.crashpad.database.initialized on file /var/folders/c3/ddgk3fbs6w1gm4pg4tfj0d0r0000gn/T/: Operation not permit

In [60]:
growing_list_abstract_3_scaled[2]


In [61]:
dfi.export(growing_list_abstract_3_scaled[2], 'growing_list_abstract_3_scaled.png')


[0118/155248.257902:ERROR:xattr.cc(63)] setxattr org.chromium.crashpad.database.initialized on file /var/folders/c3/ddgk3fbs6w1gm4pg4tfj0d0r0000gn/T/: Operation not permitted (1)
[0118/155248.258977:ERROR:file_io.cc(94)] ReadExactly: expected 8, observed 0
[0118/155248.260308:ERROR:xattr.cc(63)] setxattr org.chromium.crashpad.database.initialized on file /var/folders/c3/ddgk3fbs6w1gm4pg4tfj0d0r0000gn/T/: Operation not permitted (1)
[0118/155249.296221:INFO:headless_shell.cc(653)] Written to file /var/folders/c3/ddgk3fbs6w1gm4pg4tfj0d0r0000gn/T/tmpbdk357id/temp.png.
[0118/155249.645130:ERROR:xattr.cc(63)] setxattr org.chromium.crashpad.database.initialized on file /var/folders/c3/ddgk3fbs6w1gm4pg4tfj0d0r0000gn/T/: Operation not permitted (1)
[0118/155249.646120:ERROR:file_io.cc(94)] ReadExactly: expected 8, observed 0
[0118/155249.647619:ERROR:xattr.cc(63)] setxattr org.chromium.crashpad.database.initialized on file /var/folders/c3/ddgk3fbs6w1gm4pg4tfj0d0r0000gn/T/: Operation not permit

In [62]:
shrinking_list_abstract_3[2]


In [63]:
shrinking_list_abstract_3_scaled[2]


In [64]:
highest_abs_change_list_abstract_3[2]


In [65]:
highest_abs_change_list_abstract_3_scaled[2]


#### Some code for checking for certain strings

In [ ]:
if False:
    
    string = 'apr'

    def remove_punctuation(item):
        item = re.sub('[^a-zA-Z]', ' ', item)
        return item

    result = list(data[data['appln_abstract'].map(lambda x: remove_punctuation(x)).str.contains(string, case=False)]['appln_abstract'])
    len(result)
    

In [ ]:
string = 'apr.'

result = list(data[data['appln_abstract'].str.contains(string, case=False, regex=False)]['appln_abstract'])
len(result)


In [ ]:
result[50]
